In [5]:
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import pandas as pd
import numpy as np
from scipy import stats
import cv2
import pandas as pd
import numpy as np
from joblib import Parallel, delayed
import os
import plotly.io as pio

pio.renderers.default = "notebook"
# testing
plotly_colors = ['aliceblue', 'antiquewhite', 'aqua', 'aquamarine', 'azure', 'beige', 'bisque', 'black', 'blanchedalmond', 'blue', 'blueviolet', 'brown', 'burlywood', 'cadetblue', 'chartreuse', 'chocolate', 'coral', 'cornflowerblue', 'cornsilk', 'crimson', 'cyan', 'darkblue', 'darkcyan', 'darkgoldenrod', 'darkgray', 'darkgrey', 'darkgreen', 'darkkhaki', 'darkmagenta', 'darkolivegreen', 'darkorange', 'darkorchid', 'darkred', 'darksalmon', 'darkseagreen', 'darkslateblue', 'darkslategray', 'darkslategrey', 'darkturquoise', 'darkviolet', 'deeppink', 'deepskyblue', 'dimgray', 'dimgrey', 'dodgerblue', 'firebrick', 'floralwhite', 'forestgreen', 'fuchsia', 'gainsboro', 'ghostwhite', 'gold', 'goldenrod', 'gray', 'grey', 'green', 'greenyellow', 'honeydew', 'hotpink', 'indianred', 'indigo', 'ivory', 'khaki', 'lavender', 'lavenderblush', 'lawngreen', 'lemonchiffon', 'lightblue', 'lightcoral', 'lightcyan', 'lightgoldenrodyellow', 'lightgray', 'lightgrey', 'lightgreen', 'lightpink', 'lightsalmon', 'lightseagreen', 'lightskyblue', 'lightslategray', 'lightslategrey', 'lightsteelblue', 'lightyellow', 'lime', 'limegreen', 'linen', 'magenta', 'maroon', 'mediumaquamarine', 'mediumblue', 'mediumorchid', 'mediumpurple', 'mediumseagreen', 'mediumslateblue', 'mediumspringgreen', 'mediumturquoise', 'mediumvioletred', 'midnightblue', 'mintcream', 'mistyrose', 'moccasin', 'navajowhite', 'navy', 'oldlace', 'olive', 'olivedrab', 'orange', 'orangered', 'orchid', 'palegoldenrod', 'palegreen', 'paleturquoise', 'palevioletred', 'papayawhip', 'peachpuff', 'peru', 'pink', 'plum', 'powderblue', 'purple', 'rebeccapurple', 'red', 'rosybrown', 'royalblue', 'saddlebrown', 'salmon', 'sandybrown', 'seagreen', 'seashell', 'sienna', 'silver', 'skyblue', 'slateblue', 'slategray', 'slategrey', 'snow', 'springgreen', 'steelblue', 'tan', 'teal', 'thistle', 'tomato', 'turquoise', 'violet', 'wheat', 'white', 'whitesmoke', 'yellow', 'yellowgreen']


# Global vars

In [7]:
# wk_dir = '/data/nil-external/dcl/Events152_fMRI_NeuralMechanisms/voxelwiseAnalyses/knitr_tan/median_correlation_with_shifts'
wk_dir = os.getcwd() # will return the directory that this file is in
movie_dir = 'movies/'
output_visual_features = 'movie_visual_stats/'
output_downsampled_features = "out_convo_visual/"
movies = ['1.2.3', '6.3.9', '3.1.3', '2.4.1']

In [8]:
wk_dir

'/data/nil-external/dcl/Events152_fMRI_NeuralMechanisms/voxelwiseAnalyses/knitr_tan/median_correlation_with_shifts'

In [9]:
# read Schaefer 400 parcellation and construct a dataframe to join with correlation dataframe
# txt file was fetched from https://github.com/ThomasYeoLab/CBIG/blob/master/stable_projects/brain_parcellation/Schaefer2018_LocalGlobal/Parcellations/HCP/fslr32k/cifti/Schaefer2018_400Parcels_7Networks_order_info.txt
schaefer_nw_df = pd.read_csv("./Schaefer2018_400Parcels_7Networks_order_info.txt", header=None)
schaefer_nw_df = schaefer_nw_df.iloc[::2]
schaefer_nw_df['hemisphere'] = schaefer_nw_df.loc[:, 0].apply(lambda x: x.split('_')[1])
schaefer_nw_df['network'] = schaefer_nw_df.loc[:, 0].apply(lambda x: x.split('_')[2])
schaefer_nw_df['parcel'] = np.arange(400) + 1
schaefer_nw_df.drop(columns=[0], inplace=True)
schaefer_nw_df

hemisphere  network  parcel
0           LH      Vis       1
2           LH      Vis       2
4           LH      Vis       3
6           LH      Vis       4
8           LH      Vis       5
..         ...      ...     ...
790         RH  Default     396
792         RH  Default     397
794         RH  Default     398
796         RH  Default     399
798         RH  Default     400

[400 rows x 3 columns]

In [12]:
vis_left_parcels = schaefer_nw_df[(schaefer_nw_df.network == "Vis") & (schaefer_nw_df.hemisphere == "LH")]['parcel']

# Replicate XCP results from Matt

Tan ran xcp_36p for subject 37, the data is saved in the root directory (Events152...). Matt's old results were moved to Events152/voxelwiseAnalyses/median.../xcp_36p_despike/...

In [5]:
run_id = 1
sub_id = 37
xcp_tbl_old = pd.read_csv(f"../../xcp_36p_despike/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
xcp_tbl_old.columns = np.arange(1, len(xcp_tbl_old.columns) + 1)

xcp_tbl_new = pd.read_csv(f"../../../XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
xcp_tbl_new.columns = np.arange(1, len(xcp_tbl_new.columns) + 1)

In [6]:
fig = make_subplots(rows=31, cols=1)
c = 1
for parcel in schaefer_nw_df[(schaefer_nw_df.network == "Vis") & (schaefer_nw_df.hemisphere == "LH")]['parcel']:
    fig.add_trace(go.Scatter(opacity=0.3, y=xcp_tbl_old.iloc[:, int(parcel)], x=np.arange(len(xcp_tbl_old)), name=f"p{parcel}_Matt"), row=c, col=run_id)
    fig.add_trace(go.Scatter(opacity=0.3, y=xcp_tbl_old.iloc[:, int(parcel)], x=np.arange(len(xcp_tbl_new)), name=f"p{parcel}_Tan"), row=c, col=run_id)
    c += 1
fig.update_layout(height=31*400, title_text=f"Matt's xcp_36p_despike and Tan's xcp_36p_despike, sub-{sub_id} run-{run_id}")
fig.write_html("./plotly_figures/check_replication_xcp.html")
fig.show()


# Timeseries against Movement/Pixel Change

Tan ran xcp with a new config (24p_gsr) as recommended by Jo (from the paper analyzing naturalistic stimuli). Comparing two xcp config outputs against movement and the input (fmriprep, np2)
Tan picked subject 02 because the movement is not too bad, but substantial enough to see the effect of XCP processing.

In [5]:
# pixel_change = pd.read_csv(f"out_convo_visual/conv_{movies[run_id]}_pixel_change_mean_dtFix.csv", header=None)
# pixel_change

In [7]:
fp_names = ["trans_x","trans_y","trans_z","rot_x","rot_y","rot_z"];   # x y z roll pitch yaw order,  as named in desc-confounds_regressors.tsv
# "RotX","RotY","RotZ" in radians https://fmriprep.readthedocs.io/en/1.1.0/_modules/fmriprep/workflows/bold/confounds.html
desc_confound = pd.read_csv(f"../../../fmriprep/fmriprep/sub-02/func/sub-02_task-movie_run-1_desc-confounds_timeseries.tsv", delimiter='\t')
movement = desc_confound[fp_names]
movement

trans_x   trans_y   trans_z     rot_x     rot_y     rot_z
0    0.037155  0.160565  0.061751 -0.001113 -0.000000  0.000000
1    0.025539  0.143562  0.038320 -0.000812 -0.000000  0.000000
2    0.019457  0.183331  0.049275 -0.000419 -0.000000 -0.000308
3    0.024720  0.189319  0.060773 -0.000715 -0.000000 -0.000311
4    0.030228  0.189242  0.054566 -0.000794 -0.000222 -0.000472
..        ...       ...       ...       ...       ...       ...
400 -0.027109  0.744576  0.028757 -0.011161  0.003757  0.000378
401 -0.043823  0.818511  0.038253 -0.011634  0.003498  0.000309
402 -0.055441  0.738230  0.015615 -0.011387  0.003951  0.000004
403 -0.051728  0.800404 -0.023887 -0.010734  0.003679  0.000310
404 -0.052722  0.746404  0.031527 -0.011458  0.003802  0.000235

[405 rows x 6 columns]

In [8]:
run_ids = [1, 2, 3, 4]
chapter_names = ['exercise', 'cleaning', 'breakfast', 'bathroom']
sub_ids = ['02', '33']


In [9]:
def load_and_plot(sub_id):
    fig = make_subplots(rows=5, cols=4, 
    shared_xaxes='columns',
    subplot_titles=["movements"]*4 + ["fmriprep"]*4 + ["xcp_24p (NO global signal reg)"]*4 + ["xcp_24p_gsr (global signal reg)"]*4 + ["xcp_36p_despike (global signal reg)"]*4,
    vertical_spacing=0.05, horizontal_spacing=0.05)
    for run_id in run_ids:
        desc_confound = pd.read_csv(f"../../../fmriprep/fmriprep/sub-{sub_id}/func/sub-{sub_id}_task-movie_run-{run_id}_desc-confounds_timeseries.tsv", delimiter='\t')
        movement = desc_confound[fp_names]
        # plot movement variables
        for c in movement.columns:
            if 'rot' in c:
                fig.add_trace(go.Scatter(legendgroup=c, name=c, x=np.arange(len(movement[c])), y=movement[c]*(180/np.pi), mode="lines"), row=1, col=run_id)
            else:
                fig.add_trace(go.Scatter(legendgroup=c, name=c, x=np.arange(len(movement[c])), y=movement[c], mode="lines"), row=1, col=run_id)


        np2 = pd.read_csv(f"../../np2/sub-{sub_id}_run-{run_id}_np2_Sch400x7.txt", delimiter="\t")
        np2 = np2.iloc[:, 2:]
        np2.columns = [int(x.replace("Mean_", "")) for x in np2.columns]
        
        xcp_fc36p = pd.read_csv(f"../../xcp_36p_despike/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
        xcp_fc36p.columns = np.arange(1, len(xcp_fc36p.columns) + 1)

        xcp_fc24p_gsr = pd.read_csv(f"../../xcp_24p_gsr/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
        xcp_fc24p_gsr.columns = np.arange(1, len(xcp_fc24p_gsr.columns) + 1)

        xcp_fc24p = pd.read_csv(f"../../xcp_24p/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
        xcp_fc24p.columns = np.arange(1, len(xcp_fc24p.columns) + 1)
        
        # plot visual-average activity for np2, xcp_36p_despike, xcp_24p_gsr
        fig.add_trace(go.Scatter(legendgroup=f"average_np2", name=f"average_np2", x=np.arange(len(np2)), y=np2.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=2, col=run_id)
        fig.add_trace(go.Scatter(legendgroup=f"average_24p", name=f"average_24p", x=np.arange(len(xcp_fc24p)), y=xcp_fc24p.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=3, col=run_id)
        fig.add_trace(go.Scatter(legendgroup=f"average_24p_gsr", name=f"average_24p_gsr", x=np.arange(len(xcp_fc24p_gsr)), y=xcp_fc24p_gsr.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=4, col=run_id)
        fig.add_trace(go.Scatter(legendgroup=f"average_36p_despike", name=f"average_36p_despike", x=np.arange(len(xcp_fc36p)), y=xcp_fc36p.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=5, col=run_id)
        # plot individual parcel activitiy
        # for p in vis_left_parcels:
        #     fig.add_trace(go.Scatter(name=f"pc{p}_36p_despike", x=np.arange(len(xcp_fc36p)), y=xcp_fc36p.loc[:, p], mode="markers", fillcolor=plotly_colors[int(p)], opacity=0.1), row=2, col=run_id)
        #     fig.add_trace(go.Scatter(name=f"pc{p}_24p_gsr", x=np.arange(len(xcp_fc24p)), y=xcp_fc24p.loc[:, p], mode="markers", fillcolor=plotly_colors[int(p)], opacity=0.1), row=3, col=run_id)
        fig.add_annotation(dict(text=f"{chapter_names[run_id-1]}", font=dict(size=20)), row=1, col=run_id)

    fig.update_layout(width=1000 * 4, height=1000, title_text=f"Average Activity of Left-Vis Parcels for Sub-{sub_id} with Different Preprocessings")
    fig.update_xaxes(title_text="frames", row=5)
    fig.write_html(f"./plotly_figures/sub-{sub_id}_vis_avg_parcel.html")
    fig.show()


In [10]:
load_and_plot(sub_id='02')

In [12]:
load_and_plot(sub_id='33')

In [ ]:
# sub_id = '02'
# run_id = 2
# xcp_fc36p = pd.read_csv(f"../../xcp_36p_despike/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
# xcp_fc36p.columns = np.arange(1, len(xcp_fc36p.columns) + 1)

# xcp_fc24p_gsr = pd.read_csv(f"../../xcp_24p_gsr/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
# xcp_fc24p_gsr.columns = np.arange(1, len(xcp_fc24p_gsr.columns) + 1)

# xcp_fc24p = pd.read_csv(f"../../xcp_24p/XCP_OUTPUT_{sub_id}/sub-{sub_id}/run-{run_id}/fcon/schaefer400x7/sub-{sub_id}_run-{run_id}_schaefer400x7_ts.1D", delimiter=" ", header=None)
# xcp_fc24p.columns = np.arange(1, len(xcp_fc24p.columns) + 1)

# np2 = pd.read_csv(f"../../np2/sub-{sub_id}_run-{run_id}_np2_Sch400x7.txt", delimiter="\t")
# np2 = np2.iloc[:, 2:]
# np2.columns = [int(x.replace("Mean_", "")) for x in np2.columns]

In [14]:
# fig = make_subplots(rows=5, cols=1, shared_xaxes=True)

# # plot movement variables
# for c in movement.columns:
#     if 'rot' in c:
#         fig.add_trace(go.Scatter(name=c, x=np.arange(len(movement[c])), y=movement[c]*(180/np.pi), mode="lines"), row=1, col=1)
#     else:
#         fig.add_trace(go.Scatter(name=c, x=np.arange(len(movement[c])), y=movement[c], mode="lines"), row=1, col=1)
# # plot visual-average activity for np2, xcp_36p_despike, xcp_24p_gsr
# fig.add_trace(go.Scatter(name=f"average_np2", x=np.arange(len(np2)), y=np2.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=2, col=1)
# fig.add_trace(go.Scatter(name=f"average_36p_despike", x=np.arange(len(xcp_fc36p)), y=xcp_fc36p.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=3, col=1)
# fig.add_trace(go.Scatter(name=f"average_24p_gsr", x=np.arange(len(xcp_fc24p_gsr)), y=xcp_fc24p_gsr.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=4, col=1)
# fig.add_trace(go.Scatter(name=f"average_24p", x=np.arange(len(xcp_fc24p)), y=xcp_fc24p.loc[:, vis_left_parcels].mean(axis=1), mode="lines", fillcolor=plotly_colors[0], opacity=1), row=5, col=1)
# # plot individual parcel activitiy
# # for p in vis_left_parcels:
# #     fig.add_trace(go.Scatter(name=f"pc{p}_36p_despike", x=np.arange(len(xcp_fc36p)), y=xcp_fc36p.loc[:, p], mode="markers", fillcolor=plotly_colors[int(p)], opacity=0.1), row=2, col=1)
# #     fig.add_trace(go.Scatter(name=f"pc{p}_24p_gsr", x=np.arange(len(xcp_fc24p)), y=xcp_fc24p.loc[:, p], mode="markers", fillcolor=plotly_colors[int(p)], opacity=0.1), row=3, col=1)

# fig.update_layout(width=1000, height=700, title_text=f"sub {sub_id} run {run_id}")
# fig.show()

Looking at the generated plots above, it looks like xcp_36p and xcp_24p are not much different. fmriPrep (np2) are different from xcp output (e.g. frames 70 or 290 where np2 signals are big due to movement, but xcp signals are kind of medium).

# Correlations with PCM for two Configs

In [13]:
in_corr_xcp_24p_gsr = pd.read_csv("./visual_xcp_24p_gsr_corrs_1_550/xcp_24p_gsrCorrs_pixel_change_mean_run1_sch.txt", delimiter=" ")
in_corr_xcp_36p_despike = pd.read_csv("./visual_xcp_36p_despike_corrs_1_550/xcp_36p_despikeCorrs_pixel_change_mean_run1_sch.txt", delimiter=" ")
in_corr_xcp_24p_gsr

sub.id        p1        p2        p3        p4        p5        p6  \
1   sub-01  0.150118  0.106103  0.157626  0.189753  0.212255  0.152948   
2   sub-02 -0.042289 -0.022831 -0.016592  0.015413  0.044694 -0.076094   
3   sub-03  0.081392  0.075694  0.240980  0.218859  0.303810  0.217129   
4   sub-04  0.140788  0.158022  0.106459  0.198769  0.117521  0.165794   
5   sub-05 -0.028323 -0.110018  0.119155  0.056032  0.121804  0.132298   
6   sub-06  0.100149  0.096262  0.074897 -0.016904  0.099117  0.111834   
7   sub-07  0.146186  0.136602  0.173317  0.104592  0.112807  0.320999   
8   sub-08  0.099161  0.138135  0.117391 -0.038993  0.057138  0.174501   
9   sub-09 -0.139496 -0.129347 -0.008897 -0.096971  0.004680 -0.010293   
10  sub-11 -0.022909 -0.024269  0.080940  0.004333  0.121670  0.177649   
11  sub-12  0.205039  0.095396  0.149624  0.072049  0.061243  0.126184   
12  sub-13  0.087776 -0.000865  0.058970  0.058079 -0.105647 -0.045291   
13  sub-14  0.134086  0.151362  0.193512  0.159393  0.213929  0.298173   
14  sub-15  0.017573  0.061338 -0.036072  0.062320  0.078234  0.039976   
15  sub-16  0.124399  0.026732  0.150210  0.171556  0.180342  0.146115   
16  sub-17  0.092337  0.108482  0.225017 -0.012643  0.102272  0.100646   
17  sub-18  0.151561  0.146921  0.206207  0.105986  0.147559  0.207245   
18  sub-19  0.064201 -0.007115  0.110755  0.053665  0.003774  0.150093   
19  sub-20  0.235301  0.197873  0.235289  0.121334  0.195725  0.141864   
20  sub-21  0.071656  0.122437  0.082270  0.075942  0.042599  0.066335   
21  sub-22  0.213891  0.214911  0.210965  0.127068  0.213689  0.166749   
22  sub-23  0.099250  0.027694  0.108103 -0.016205 -0.037780  0.112399   
23  sub-24  0.107767  0.019693  0.060302  0.031013  0.059894  0.137219   
24  sub-25  0.044683  0.061647  0.088855 -0.125798 -0.201964 -0.123624   
25  sub-26 -0.037880  0.145443  0.098502  0.139890  0.071247  0.052537   
26  sub-27  0.103651  0.114684  0.043533  0.238145  0.297177  0.081844   
27  sub-28  0.185980  0.217717  0.120901  0.041176  0.073539  0.063355   
28  sub-29  0.051177  0.011460  0.100485  0.060227  0.042771  0.107061   
29  sub-30  0.149732  0.218569  0.126371  0.054786  0.023673  0.141515   
30  sub-31  0.039663  0.028694 -0.013004  0.138209  0.202126  0.062759   
31  sub-33  0.065906  0.021631  0.013135  0.091484  0.095449  0.043794   
32  sub-34 -0.002352  0.047710  0.023792  0.038276  0.056387  0.015798   
33  sub-35 -0.086772  0.058745  0.022466 -0.054993 -0.021585  0.194177   
34  sub-36  0.113891  0.157742  0.138738  0.230533  0.100540 -0.047823   
35  sub-37 -0.055097  0.096835 -0.021897 -0.007629  0.162081  0.037110   

          p7        p8        p9  ...      p391      p392      p393      p394  \
1  -0.146724  0.204902  0.129228  ...  0.063863 -0.058428  0.000543  0.003199   
2  -0.014189  0.046324  0.057591  ... -0.199836 -0.098176 -0.067332 -0.067207   
3   0.040253  0.209489  0.265189  ... -0.213296 -0.124085 -0.034403 -0.142313   
4   0.136982  0.096715  0.135714  ... -0.099502 -0.001002 -0.084568 -0.106602   
5  -0.077420  0.118727  0.072838  ... -0.027958 -0.133246  0.084321 -0.006499   
6   0.051893  0.175177  0.199896  ... -0.095155  0.112365 -0.023962  0.018519   
7   0.111094  0.280568  0.144728  ... -0.194023  0.124191 -0.005584 -0.097992   
8   0.005790  0.197990  0.206458  ... -0.160568 -0.045721 -0.006333 -0.024698   
9  -0.048225  0.023734  0.191652  ... -0.080079 -0.016053 -0.072048 -0.124144   
10 -0.101503  0.129769  0.096226  ... -0.040052 -0.137917 -0.032622 -0.064654   
11  0.007349  0.262485  0.100268  ...  0.084508 -0.072837  0.166948 -0.072698   
12 -0.099625  0.283615 -0.063955  ...  0.004440 -0.022418  0.086577  0.036094   
13  0.035866  0.176374  0.218802  ...  0.072147  0.029209 -0.029354 -0.044452   
14 -0.019585  0.018658  0.166080  ...  0.020277 -0.039581  0.016432  0.007961   
15 -0.044271  0.049745  0.103350  ... -0.003349  0.085142 -0.051933  0.119315   
16  0.076183  0.165407  0.251366  ... -0.00

In [25]:
join_df = pd.merge(in_corr_xcp_24p_gsr, in_corr_xcp_36p_despike, on='sub.id', suffixes = ("_24p_gsr","_36p_despike"))
join_df

sub.id  p1_24p_gsr  p2_24p_gsr  p3_24p_gsr  p4_24p_gsr  p5_24p_gsr  \
0   sub-01    0.150118    0.106103    0.157626    0.189753    0.212255   
1   sub-02   -0.042289   -0.022831   -0.016592    0.015413    0.044694   
2   sub-03    0.081392    0.075694    0.240980    0.218859    0.303810   
3   sub-04    0.140788    0.158022    0.106459    0.198769    0.117521   
4   sub-05   -0.028323   -0.110018    0.119155    0.056032    0.121804   
5   sub-06    0.100149    0.096262    0.074897   -0.016904    0.099117   
6   sub-07    0.146186    0.136602    0.173317    0.104592    0.112807   
7   sub-08    0.099161    0.138135    0.117391   -0.038993    0.057138   
8   sub-09   -0.139496   -0.129347   -0.008897   -0.096971    0.004680   
9   sub-11   -0.022909   -0.024269    0.080940    0.004333    0.121670   
10  sub-12    0.205039    0.095396    0.149624    0.072049    0.061243   
11  sub-13    0.087776   -0.000865    0.058970    0.058079   -0.105647   
12  sub-14    0.134086    0.151362    0.193512    0.159393    0.213929   
13  sub-15    0.017573    0.061338   -0.036072    0.062320    0.078234   
14  sub-16    0.124399    0.026732    0.150210    0.171556    0.180342   
15  sub-17    0.092337    0.108482    0.225017   -0.012643    0.102272   
16  sub-18    0.151561    0.146921    0.206207    0.105986    0.147559   
17  sub-19    0.064201   -0.007115    0.110755    0.053665    0.003774   
18  sub-20    0.235301    0.197873    0.235289    0.121334    0.195725   
19  sub-21    0.071656    0.122437    0.082270    0.075942    0.042599   
20  sub-22    0.213891    0.214911    0.210965    0.127068    0.213689   
21  sub-23    0.099250    0.027694    0.108103   -0.016205   -0.037780   
22  sub-24    0.107767    0.019693    0.060302    0.031013    0.059894   
23  sub-25    0.044683    0.061647    0.088855   -0.125798   -0.201964   
24  sub-26   -0.037880    0.145443    0.098502    0.139890    0.071247   
25  sub-27    0.103651    0.114684    0.043533    0.238145    0.297177   
26  sub-28    0.185980    0.217717    0.120901    0.041176    0.073539   
27  sub-29    0.051177    0.011460    0.100485    0.060227    0.042771   
28  sub-30    0.149732    0.218569    0.126371    0.054786    0.023673   
29  sub-31    0.039663    0.028694   -0.013004    0.138209    0.202126   
30  sub-33    0.065906    0.021631    0.013135    0.091484    0.095449   
31  sub-34   -0.002352    0.047710    0.023792    0.038276    0.056387   
32  sub-35   -0.086772    0.058745    0.022466   -0.054993   -0.021585   
33  sub-36    0.113891    0.157742    0.138738    0.230533    0.100540   
34  sub-37   -0.055097    0.096835   -0.021897   -0.007629    0.162081   

    p6_24p_gsr  p7_24p_gsr  p8_24p_gsr  p9_24p_gsr  ...  p391_36p_despike  \
0     0.152948   -0.146724    0.204902    0.129228  ...          0.069927   
1    -0.076094   -0.014189    0.046324    0.057591  ...         -0.145712   
2     0.217129    0.040253    0.209489    0.265189  ...         -0.164501   
3     0.165794    0.136982    0.096715    0.135714  ...         -0.127634   
4     0.132298   -0.077420    0.118727    0.072838  ...         -0.028710   
5     0.111834    0.051893    0.175177    0.199896  ...         -0.055288   
6     0.320999    0.111094    0.280568    0.144728  ...         -0.157479   
7     0.174501    0.005790    0.197990    0.206458  ...         -0.123247   
8    -0.010293   -0.048225    0.023734    0.191652  ...         -0.073648   
9     0.177649   -0.101503    0.129769    0.096226  ...         -0.058507   
10    0.126184    0.007349    0.262485    0.100268  ...          0.084448   
11   -0.045291   -0.099625    0.283615   -0.063955  ...         -0.034860   
12    0.298173    0.035866    0.176374    0.218802  ...          0.040653   
13    0.039976   -0.019585    0.018658    0.166080  ...          0.028189   
14    0.146115   -0.044271    0.049745    0.103350  ...          0.011285   
15    0.100646    0.076183    0.165407    0.251366  ...         -0.022465   
16    0.207245    0.190740    

In [ ]:
import scipy.stats as stats

In [84]:
fig = make_subplots(rows=6, cols=6, subplot_titles=list(vis_left_parcels), shared_xaxes=True, shared_yaxes=True, vertical_spacing=0.02, horizontal_spacing=0.02)
corr_min = join_df.iloc[:, 1:].values.min()
corr_max = join_df.iloc[:, 1:].values.max()
for i, p in enumerate(vis_left_parcels):
    select_df = join_df.filter(regex=f"p{p}_")
    fig.add_trace(
        go.Scatter(x=select_df.loc[:, f"p{p}_24p_gsr"], y=select_df.loc[:, f"p{p}_36p_despike"], mode='markers', name=f"parcel_{p}"),
        row=i//6 + 1, col=i%6+1 
    )
    # corr_min = select_df.values.min()
    # corr_max = select_df.values.max()
    fig.add_trace(
        go.Scatter(x=[corr_min, corr_max], y=[corr_min, corr_max], mode="lines", legendgroup=None, name=None, line_color="black", showlegend=False),
        row=i//6 + 1, col=i%6+1 
    )
    t_stat, p_value = stats.ttest_rel(select_df.loc[:, f"p{p}_24p_gsr"], select_df.loc[:, f"p{p}_36p_despike"])
    df = len(select_df) * 2 - 2
    fig.add_annotation(x=-0.15, y=0.2, text=f"t={t_stat:.02f}, p={p_value:.01e}" + ("*" if p_value < 0.05 else ""), showarrow=False, 
    row=i//6 + 1, col=i%6+1)

fig.update_layout(width=400*6, height=400*6)
fig.update_layout(title=f"xcp_24p_gsr - xcp_36p_despike, x=24p, y=36p")
fig.show()


# Prepare for XCP commands

## Create Functional Cohort Files to run 47 participants

In [6]:
func_cohort = pd.read_csv("../../../XCPparam/func_cohort.csv")
func_cohort

id0    id1                                                img
0    sub-01  run-1  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
1    sub-01  run-2  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
2    sub-01  run-3  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
3    sub-01  run-4  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
4    sub-02  run-1  fmriprep/fmriprep/sub-02/func/sub-02_task-movi...
..      ...    ...                                                ...
143  sub-36  run-4  fmriprep/fmriprep/sub-36/func/sub-36_task-movi...
144  sub-37  run-1  fmriprep/fmriprep/sub-37/func/sub-37_task-movi...
145  sub-37  run-2  fmriprep/fmriprep/sub-37/func/sub-37_task-movi...
146  sub-37  run-3  fmriprep/fmriprep/sub-37/func/sub-37_task-movi...
147  sub-37  run-4  fmriprep/fmriprep/sub-37/func/sub-37_task-movi...

[148 rows x 3 columns]

In [17]:
for sub_id in range(38, 48):
    for run_id in [1, 2, 3, 4]:
        row = [f"sub-{sub_id}", f"run-{run_id}", f"fmriprep/fmriprep/sub-{sub_id}/func/sub-{sub_id}_task-movie_run-{run_id}_space-MNI152NLin2009cAsym_desc-preproc_bold.nii.gz"]
        func_cohort.loc[len(func_cohort)] = row
func_cohort

id0    id1                                                img
0    sub-01  run-1  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
1    sub-01  run-2  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
2    sub-01  run-3  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
3    sub-01  run-4  fmriprep/fmriprep/sub-01/func/sub-01_task-movi...
4    sub-02  run-1  fmriprep/fmriprep/sub-02/func/sub-02_task-movi...
..      ...    ...                                                ...
183  sub-46  run-4  fmriprep/fmriprep/sub-46/func/sub-46_task-movi...
184  sub-47  run-1  fmriprep/fmriprep/sub-47/func/sub-47_task-movi...
185  sub-47  run-2  fmriprep/fmriprep/sub-47/func/sub-47_task-movi...
186  sub-47  run-3  fmriprep/fmriprep/sub-47/func/sub-47_task-movi...
187  sub-47  run-4  fmriprep/fmriprep/sub-47/func/sub-47_task-movi...

[188 rows x 3 columns]

In [18]:
func_cohort.to_csv("../../../XCPparam/func_cohort_all_47.csv", index=False)

In [8]:
for sub_id in range(38, 48):
    func_cohort_sub = pd.DataFrame(columns=func_cohort.columns)
    for run_id in [1, 2, 3, 4]:
        row = [f"sub-{sub_id}", f"run-{run_id}", f"fmriprep/fmriprep/sub-{sub_id}/func/sub-{sub_id}_task-movie_run-{run_id}_space-MNI152NLin2009cAsym_desc-preproc_bold.nii.gz"]
        func_cohort_sub.loc[len(func_cohort_sub)] = row
    func_cohort_sub.to_csv(f"../../../XCPparam/func_cohort_{sub_id}.csv", index=False)

## Generate commands to preprocess Individuals

In [9]:
# for xcp_24p_gsr
design = "fc-24p_gsr.dsn"
xcp_output_dir = "xcp_24p_gsr"
with open("./XCP_24p_gsr_commands.sh", 'w') as f:
    for i in range(1, 48):
            sub_id = f"{i:02d}"
            command = f"singularity run -B /data/nil-external/dcl/Events152_fMRI_NeuralMechanisms/:/data --cleanenv ../Singularity_Image/xcpEngine3.simg -d /data/XCPparam/{design} -c /data/XCPparam/func_cohort_{sub_id}.csv -o /data/voxelwiseAnalyses/{xcp_output_dir}/XCP_OUTPUT_{sub_id} -t 1 -i /data/voxelwiseAnalyses/{xcp_output_dir}/WORKINGDIR_{sub_id} -r /data"
            f.write(command + '\n')
            

In [1]:
# for xcp_24p
design = "fc-24p.dsn"
xcp_output_dir = "xcp_24p"
with open("./XCP_24p_commands.sh", 'w') as f:
    for i in range(1, 38):
        if i not in [2, 33]:  # 2 and 33 processed
            sub_id = f"{i:02d}"
            command = f"singularity run -B /data/nil-external/dcl/Events152_fMRI_NeuralMechanisms/:/data --cleanenv ../Singularity_Image/xcpEngine3.simg -d /data/XCPparam/{design} -c /data/XCPparam/func_cohort_{sub_id}.csv -o /data/voxelwiseAnalyses/{xcp_output_dir}/XCP_OUTPUT_{sub_id} -t 1 -i /data/voxelwiseAnalyses/{xcp_output_dir}/WORKINGDIR_{sub_id} -r /data"
            f.write(command + '\n')
            